## Import data

In [ ]:
import pandas as pd
import numpy as np

interval = "4h"
klines_df = pd.read_csv(f"klines_data_{interval}.csv")
signals_df = pd.read_csv("tradingview_signals_server.csv")


signals_df["utc_time"] = pd.to_datetime(signals_df["unix_timestamp"], unit="s", utc=True).dt.floor("H")

print(signals_df[["symbol", "utc_time", "signal"]].head())


print('klines_df.shape', klines_df.shape)
klines_df.info()

     symbol                  utc_time      signal
0   BNBUSDT 2025-03-01 16:00:00+00:00  STRONG_BUY
1   BTCUSDT 2025-03-01 16:00:00+00:00     NEUTRAL
2   ETHUSDT 2025-03-01 16:00:00+00:00        SELL
3  CAKEUSDT 2025-03-01 16:00:00+00:00  STRONG_BUY
4   ETHUSDT 2025-03-01 16:00:00+00:00     NEUTRAL
klines_df.shape (16987, 7)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16987 entries, 0 to 16986
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Date    16987 non-null  object 
 1   Open    16987 non-null  float64
 2   High    16987 non-null  float64
 3   Low     16987 non-null  float64
 4   Close   16987 non-null  float64
 5   Volume  16987 non-null  float64
 6   Symbol  16987 non-null  object 
dtypes: float64(5), object(2)
memory usage: 929.1+ KB


<ipython-input-11-112cc4130af0>:9: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  signals_df["utc_time"] = pd.to_datetime(signals_df["unix_timestamp"], unit="s", utc=True).dt.floor("H")


In [ ]:
print('signals_df.shape', signals_df.shape)
signals_df.info()

signals_df.shape (32267, 9)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32267 entries, 0 to 32266
Data columns (total 9 columns):
 #   Column          Non-Null Count  Dtype              
---  ------          --------------  -----              
 0   #               32267 non-null  int64              
 1   id              32267 non-null  int64              
 2   symbol          32267 non-null  object             
 3   timeframe       32267 non-null  object             
 4   signal          32267 non-null  object             
 5   entry_price     32267 non-null  float64            
 6   unix_timestamp  32267 non-null  int64              
 7   utc_time        32267 non-null  datetime64[ns, UTC]
 8   local_time      32267 non-null  object             
dtypes: datetime64[ns, UTC](1), float64(1), int64(3), object(4)
memory usage: 2.2+ MB


In [ ]:
klines_df['Date'] = pd.to_datetime(klines_df['Date'])
signals_df['utc_time'] = pd.to_datetime(signals_df['utc_time'])

signals_df = signals_df[signals_df["timeframe"] == "1h"]

## Hyperopt_by_month

In [ ]:
!pip install backtesting
!pip install pandas_ta
!pip install hyperopt

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.1/190.1 kB 3.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.1/115.1 kB 2.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pandas_ta: filename=pandas_ta-0.3.14b0-py3-none-any.whl size=218909 sha256=3aa5a34d2dadafebc02a9f69d074c98fdfbc644b3bceed317fd68190166c4e4d
  Stored in directory: /root/.cache/pip/wheels/7f/33/8b/50b245c5c65433cd8f5cb24ac15d97e5a3db2d41a8b6ae957d
Successfully built pandas_ta


In [ ]:
import pandas as pd
from datetime import datetime
from hyperopt import fmin, tpe, hp, Trials
import backtesting
from dateutil.relativedelta import relativedelta
import traceback

def generate_monthly_intervals(start_date, end_date):
    start = datetime.strptime(start_date, "%Y-%m")
    end = datetime.strptime(end_date, "%Y-%m")
    intervals = []
    while start <= end:
        next_month = start + relativedelta(months=1)
        intervals.append((start.strftime("%Y-%m"), next_month.strftime("%Y-%m")))
        start = next_month
    return intervals

def full_period_backtest(strategy, data, initial_capital=1_000_000):
    data.index = pd.to_datetime(data.index).tz_localize(None)
    test = backtesting.Backtest(data, strategy, cash=initial_capital, commission=0.0005)
    res = test.run()
    trades = res._trades.copy()
    # print(res)
    return trades, res

from datetime import datetime
from dateutil.relativedelta import relativedelta
import pandas as pd

def analyze_monthly_results(trades, intervals, initial_capital, equity_curve):
    trades['ExitTime'] = pd.to_datetime(trades['ExitTime']).dt.tz_localize(None)
    trades['Close Time'] = pd.to_datetime(trades['ExitTime'])
    trades.set_index('Close Time', inplace=True)
    trades['Trade Duration'] = (trades['ExitTime'] - trades['EntryTime']).dt.total_seconds()

    monthly_results = {}
    total_pnl = 0
    profit_months = 0
    loss_months = 0
    total_trade_duration = 0
    total_trades = len(trades)

    capital = initial_capital  # Начальный капитал
    last_interval = intervals[-1]  # Последний месяц

    for start, end in intervals:
        start_date = datetime.strptime(start, "%Y-%m")
        end_date = datetime.strptime(end, "%Y-%m") + relativedelta(months=1, days=-1, hours=23, minutes=59, seconds=59)

        monthly_trades = trades[(trades.index >= start_date) & (trades.index <= end_date)]

        if monthly_trades.empty:
            monthly_results[start] = (0.0, 0)
            continue

        # PnL за месяц
        monthly_pnl = monthly_trades['PnL'].sum()
        capital += monthly_pnl  # Обновляем капитал только на PnL

        # Если это последний месяц, учитываем открытые позиции
        if (start, end) == last_interval and not equity_curve.empty:
            last_equity = equity_curve['Equity'].iloc[-1]  # Финальная Equity
            open_pnl = last_equity - capital  # Открытые позиции
            capital += open_pnl  # Учитываем их в капитале

        # Итоговый процент профита за месяц
        prev_capital = capital - monthly_pnl  # Капитал до учета текущего месяца
        monthly_pnl_percent = ((capital - prev_capital) / prev_capital) * 100 if prev_capital != 0 else 0

        # Средняя длительность сделки (в часах)
        avg_trade_duration = monthly_trades['Trade Duration'].mean() / 3600 if len(monthly_trades) > 0 else 0

        monthly_results[start] = (round(monthly_pnl_percent, 8), round(avg_trade_duration, 2))

        total_pnl += monthly_pnl
        total_trade_duration += monthly_trades['Trade Duration'].sum()

        if monthly_pnl_percent > 0:
            profit_months += 1
        else:
            loss_months += 1

    avg_trade_duration_total = (total_trade_duration / total_trades) / 3600 if total_trades > 0 else 0
    total_months = profit_months + loss_months
    profit_month_ratio = (profit_months / total_months * 100) if total_months > 0 else 0

    # Итоговый Return [%]
    total_return = ((capital - initial_capital) / initial_capital) * 100

    return total_return, profit_months, loss_months, monthly_results, avg_trade_duration_total, profit_month_ratio



def generate_search_space(params_to_optimize):
    space = {}
    for param, settings in params_to_optimize.items():
        if settings['type'] == 'quniform':
            space[param] = hp.quniform(param, settings['range'][0], settings['range'][1], settings.get('q', 1))
        elif settings['type'] == 'uniform':
            space[param] = hp.uniform(param, settings['range'][0], settings['range'][1])
        else:
            raise ValueError(f"Неизвестный тип параметра: {settings['type']}")
    return space

def optimize_strategy(data, symbol, interval, start_date, end_date, shared_folder_path, max_evals, params_to_optimize, fixed_params, strategy):
    intervals = generate_monthly_intervals(start_date, end_date)
    trials = Trials()
    space = generate_search_space(params_to_optimize)
    results = []

    print(f"Общее количество строк в загруженных данных: {len(data)}")
    print(f"Диапазон дат: {data.index.min()} - {data.index.max()}")
    print(f"Оптимизация для {symbol} ({interval}) с {start_date} по {end_date} началась...\n")

    def objective(params):
        for key, value in fixed_params.items():
            setattr(strategy, key, value)

        for key, value in params.items():
            setattr(strategy, key, int(value) if 'length' in key else value)

        print(f"Параметры: {params}, {fixed_params}")

        try:
            trades, res = full_period_backtest(strategy, data, 1_000_000)

            total_pnl, profit_months, loss_months, monthly_results, avg_trade_duration, profit_month_ratio = analyze_monthly_results(
                trades, intervals, 1_000_000, res._equity_curve
            )

            print(f"Общий профит: {total_pnl:.2f}%, Профитные месяцы: {profit_months}, Убыточные месяцы: {loss_months}, Процент профитных месяцев: {profit_month_ratio:.2f}%")
            print(f"Результаты по месяцам: {[(month, pnl) for month, (pnl, _) in monthly_results.items()]}\n")

            row = {
                'symbol': symbol,
                'interval': interval,
                **{key: fixed_params.get(key, None) for key in fixed_params},
                **{key: (int(value) if 'length' in key else value) for key, value in params.items()},
                'strategy': strategy.__name__,
                'total_pnl%': total_pnl,
                'avg_trade_duration_hours': avg_trade_duration,
                'profit_month_count': profit_months,
                'loss_month_count': loss_months,
                'profit_month_ratio%': profit_month_ratio
            }

            for month, (pnl, _) in monthly_results.items():
                row[month] = pnl

            results.append(row)
            return {'loss': -total_pnl, 'status': 'ok', 'params': params}

        except Exception as e:
            print("Ошибка в objective:", e)
            print(traceback.format_exc())  # Логирование полной трассировки ошибки
            return {'loss': float('inf'), 'status': 'fail', 'params': params}

    try:
        fmin(objective, space, algo=tpe.suggest, max_evals=max_evals, trials=trials)
    except Exception as e:
        print("Ошибка при выполнении fmin:", e)
        print(traceback.format_exc())
        return None

    results_df = pd.DataFrame(results)
    save_results_to_csv(results_df, shared_folder_path, "hyperopt_optimization_results.csv")

    if trials.trials:
        best_trial = min(trials.trials, key=lambda x: x['result']['loss'])
        best_params = best_trial['result']['params']
        best_loss = best_trial['result']['loss']
        return best_params, -best_loss
    else:
        print("Не удалось найти лучшие параметры.")
        return None


# best_params, total_pnl = optimize_strategy(
#     data=df,
#     symbol=symbol,
#     interval=interval,
#     start_date=start_date,
#     end_date=end_date,
#     max_evals=max_evals,
#     shared_folder_path=shared_folder_path,
#     params_to_optimize=params_to_optimize,
#     fixed_params=fixed_params
# )

# # Настройка стратегии с оптимизированными параметрами
# SlopingStrategy.window_length = fixed_params.get('window_length') or int(best_params['window_length'])
# SlopingStrategy.min_space = fixed_params.get('min_space') or int(best_params['min_space'])
# SlopingStrategy.sloping_atr_length = fixed_params.get('sloping_atr_length') or int(best_params['sloping_atr_length'])
# SlopingStrategy.take_profit_multiplier = fixed_params.get('take_profit_multiplier') or best_params['take_profit_multiplier']
# SlopingStrategy.stop_loss_multiplier = fixed_params.get('stop_loss_multiplier') or best_params['stop_loss_multiplier']

# print("\nНастройка стратегии завершена.")

# # Тестируем стратегию
# test = backtesting.Backtest(data=df, strategy=SlopingStrategy, cash=1_000_000, commission=0.0005)
# res = test.run()

# print(symbol)
# print()
# print("Результаты с оптимизированными параметрами:", res)
# print('Window length', SlopingStrategy.window_length)
# print('Min space', SlopingStrategy.min_space)
# print('Sloping atr length', SlopingStrategy.sloping_atr_length)
# print('Take profit multiplier', SlopingStrategy.take_profit_multiplier)
# print('Stop loss multiplier', SlopingStrategy.stop_loss_multiplier)

/usr/local/lib/python3.11/dist-packages/backtesting/_plotting.py:55: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support, such as old IDEs. Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


## Strategy

In [ ]:
import pandas as pd
import numpy as np
import pandas_ta as ta
from backtesting import Backtest, Strategy

trade_log = []
class SignalStrategy(Strategy):
    stop_loss_multiplier = 0.4
    take_profit_multiplier = 1.2
    signals_df = None
    symbol = None

    def init(self):
        """Load trading signals and ATR indicator"""
        self.signals = self.signals_df[self.signals_df["symbol"] == self.symbol]
        self.used_signals = set()

        def atr_indicator(h, l, c):
            """Calculate ATR (Average True Range)"""
            try:
                atr_values = ta.atr(pd.Series(h), pd.Series(l), pd.Series(c), length=14)
                return atr_values.fillna(0).to_numpy() if atr_values is not None else np.zeros(len(h))
            except Exception as e:
                print(f"Error calculating ATR: {e}")
                return np.zeros(len(h))

        self.atr = self.I(atr_indicator, self.data.High, self.data.Low, self.data.Close)

    def next(self):
        """Process signals and open trades accordingly"""
        current_time = self.data.index[-1]
        current_price = self.data.Close[-1]
        current_atr = self.atr[-1]

        if current_atr == 0 or pd.isna(current_atr):
            return

        for _, signal in self.signals.iterrows():
            signal_time = signal['utc_time']

            if signal_time in self.used_signals:
                continue

            if signal_time in self.data.index:
                self.used_signals.add(signal_time)

                if signal['signal'] == "STRONG_BUY" and not self.position:
                    stop_loss = current_price - (self.stop_loss_multiplier * current_atr)
                    take_profit = current_price + (self.take_profit_multiplier * current_atr)

                    if stop_loss < current_price < take_profit:
                        print(f"🚀 LONG {self.symbol} | {current_time} | Price: {current_price} | SL: {stop_loss:.4f} | TP: {take_profit:.4f}")
                        self.buy(sl=stop_loss, tp=take_profit)

                elif signal['signal'] == "STRONG_SELL" and not self.position:
                    stop_loss = current_price + (self.stop_loss_multiplier * current_atr)
                    take_profit = current_price - (self.take_profit_multiplier * current_atr)

                    if take_profit < current_price < stop_loss:
                        print(f"🚨 SHORT {self.symbol} | {current_time} | Price: {current_price} | SL: {stop_loss:.4f} | TP: {take_profit:.4f}")
                        self.sell(sl=stop_loss, tp=take_profit)

    def notify_trade(self, trade):
        """Log trade results when a trade is closed"""
        if trade.is_closed:
            trade_log.append({
                "Symbol": self.symbol,
                "Entry Time": trade.entry_time,
                "Exit Time": trade.exit_time,
                "Entry Price": trade.entry_price,
                "Exit Price": trade.exit_price,
                "Return [%]": trade.pl_pct * 100,
            })


## Backtesting

In [ ]:
import pandas as pd
import numpy as np
import pandas_ta as ta
from backtesting import Backtest, Strategy


results_list = []


for symbol in klines_df["Symbol"].unique():
    print(f"🔍 Testing {symbol}...")

    data = klines_df[klines_df["Symbol"] == symbol].copy()
    data['Date'] = pd.to_datetime(data['Date'])
    data.set_index("Date", inplace=True)

    if not isinstance(data.index, pd.DatetimeIndex):
        print(f"⚠️ Index for {symbol} is not DatetimeIndex, attempting to convert...")
        data.index = pd.to_datetime(data.index)

    data.drop(columns=["Symbol"], inplace=True)

    symbol_signals = signals_df[(signals_df["symbol"] == symbol) & (signals_df["timeframe"] == f"{interval}")]
    unique_signals_count = symbol_signals["utc_time"].nunique()

    if symbol_signals.empty:
        print(f"⚠️ No signals for {symbol}, skipping...")
        continue

    print(f"📊 Found {len(symbol_signals)} signals ({unique_signals_count} unique) for {symbol}")

    SignalStrategy.signals_df = signals_df
    SignalStrategy.symbol = symbol

    bt = Backtest(data, SignalStrategy, cash=1_000_000, commission=0.0005)
    stats = bt.run()

    total_profit = sum(t["Return [%]"] for t in trade_log if t["Return [%]"] > 0)
    total_loss = sum(t["Return [%]"] for t in trade_log if t["Return [%]"] < 0)

    results = {
        "Symbol": symbol,
        "Total Trades": stats["# Trades"],
        "Win Rate": stats["Win Rate [%]"],
        "Return [%]": stats["Return [%]"],
        "Total Profit [%]": total_profit,
        "Total Loss [%]": total_loss,
        "Final Return [%]": total_profit + total_loss
    }
    results_list.append(results)

    print(f"✅ {symbol} — Return: {results['Return [%]']:.2f}%, Trades: {results['Total Trades']}, Win Rate: {results['Win Rate']:.2f}%, Profit: {results['Total Profit [%]']:.2f}%, Loss: {results['Total Loss [%]']:.2f}%\n")

results_df = pd.DataFrame(results_list)
results_df.to_csv(f"backtest_results_{interval}.csv", index=False)
trade_log_df = pd.DataFrame(trade_log)
trade_log_df.to_csv("trade_log.csv", index=False)

print("📌 Backtest completed! Results saved in backtest_results.csv")
print("📌 Trade log saved in trade_log.csv")

display(results_df)


🔍 Testing BNBUSDT...
📊 Found 7 signals (7 unique) for BNBUSDT


Backtest.run:   0%|          | 0/53 [00:00<?, ?it/s]

🚀 LONG BNBUSDT | 2025-03-03 04:00:00+00:00 | Price: 607.75 | SL: 603.1152 | TP: 621.6543
🚀 LONG BNBUSDT | 2025-03-03 04:00:00+00:00 | Price: 607.75 | SL: 603.1152 | TP: 621.6543
🚨 SHORT BNBUSDT | 2025-03-03 20:00:00+00:00 | Price: 576.1 | SL: 581.6857 | TP: 559.3428
🚨 SHORT BNBUSDT | 2025-03-04 04:00:00+00:00 | Price: 564.91 | SL: 570.9766 | TP: 546.7101
🚀 LONG BNBUSDT | 2025-03-06 04:00:00+00:00 | Price: 604.68 | SL: 599.6478 | TP: 619.7767


/usr/local/lib/python3.11/dist-packages/backtesting/backtesting.py:955: UserWarning: time=15: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(


🚨 SHORT BNBUSDT | 2025-03-07 00:00:00+00:00 | Price: 593.76 | SL: 598.7752 | TP: 578.7144
🚨 SHORT BNBUSDT | 2025-03-09 00:00:00+00:00 | Price: 588.42 | SL: 592.1813 | TP: 577.1360
🚨 SHORT BNBUSDT | 2025-03-09 12:00:00+00:00 | Price: 566.73 | SL: 570.5260 | TP: 555.3419
🚨 SHORT BNBUSDT | 2025-03-09 16:00:00+00:00 | Price: 560.56 | SL: 564.6772 | TP: 548.2083
✅ BNBUSDT — Return: -0.14%, Trades: 7, Win Rate: 28.57%, Profit: 0.00%, Loss: 0.00%

🔍 Testing BTCUSDT...
📊 Found 54 signals (54 unique) for BTCUSDT


...

/usr/local/lib/python3.11/dist-packages/backtesting/backtesting.py:955: UserWarning: time=15: Broker canceled the relative-sized order due to insufficient margin.
  warnings.warn(


✅ GPSUSDT — Return: -18.32%, Trades: 4, Win Rate: 0.00%, Profit: 0.00%, Loss: 0.00%

🔍 Testing REDUSDT...
📊 Found 8 signals (8 unique) for REDUSDT


Backtest.run:   0%|          | 0/52 [00:00<?, ?it/s]

🚨 SHORT REDUSDT | 2025-03-06 20:00:00+00:00 | Price: 0.6822 | SL: 0.7443 | TP: 0.4959
🚨 SHORT REDUSDT | 2025-03-07 16:00:00+00:00 | Price: 0.6847 | SL: 0.7402 | TP: 0.5182
🚨 SHORT REDUSDT | 2025-03-09 12:00:00+00:00 | Price: 0.4902 | SL: 0.5257 | TP: 0.3836
✅ REDUSDT — Return: 14.90%, Trades: 2, Win Rate: 50.00%, Profit: 0.00%, Loss: 0.00%

📌 Backtest completed! Results saved in backtest_results.csv
📌 Trade log saved in trade_log.csv


Symbol  Total Trades   Win Rate  Return [%]  Total Profit [%]  \
0     BNBUSDT             7  28.571429   -0.138306                 0   
1     BTCUSDT             3  33.333333    0.594398                 0   
2     ETHUSDT             4  25.000000    1.079228                 0   
3    CAKEUSDT             9  55.555556   12.976374                 0   
4      SCUSDT            13  30.769231    1.327111                 0   
..        ...           ...        ...         ...               ...   
310   APTUSDT             9  33.333333    4.509617                 0   
311   FXSUSDT             8  50.000000    9.645027                 0   
312  AVAXUSDT            12  33.333333    3.902535                 0   
313   GPSUSDT             4   0.000000  -18.316229                 0   
314   REDUSDT             2  50.000000   14.895556                 0   

     Total Loss [%]  Final Return [%]  
0                 0                 0  
1                 0                 0  
2                 0                 0  
3                 0                 0  
4                 0                 0  
..              ...               ...  
310               0                 0  
311               0                 0  
312               0                 0  
313               0                 0  
314               0                 0  

[315 rows x 7 columns]

### Hypeopt_by_month

In [ ]:
symbol_1 = 'BTCUSDT'
interval_1 = '1h'
start_date_1 = '2023-12'
end_date_1 = '2025-02'
max_evals_1 = 50


# Параметры для оптимизации
params_to_optimize_1 = {
    'atr_period': {'type': 'quniform', 'range': (7, 50, 1)},
    'multiplier': {'type': 'uniform', 'range': (1.0, 3.5)},
    'ema_period': {'type': 'quniform', 'range': (7, 50, 1)}

}

fixed_params_1 = {}
# # Фиксированные параметры
# fixed_params_1 = {
#     'min_space': 5,
#     # 'window_length': 50,
#     # 'sloping_atr_length': 20,
#     # 'take_profit_multiplier': 1.5,
#     # 'stop_loss_multiplier': 0.5
# }
fixed_params_1 = {}

In [ ]:
# Настройка и вызов оптимизации
# symbol = 'SUIUSDT'
# interval = '1h'
# start_date = '2024-11'
# end_date = '2024-11'

symbol = symbol_1
interval = interval_1
start_date = start_date_1
end_date = end_date_1
max_evals = max_evals_1
params_to_optimize=params_to_optimize_1
fixed_params=fixed_params_1
strategy = SuperTrendStrategy

# Загрузка данных
df = download_klines(symbol, interval, start_date, end_date)
print(symbol, interval)
print(f"Общее количество строк в загруженных данных: {len(df)}")
print(f"Диапазон дат: {df.index.min()} - {df.index.max()}")

## Final data

In [ ]:
import pandas as pd

klines_df = pd.read_csv("klines_data_1h.csv")
signals_df = pd.read_csv("tradingview_signals_server.csv")
interval = '1h'

df = signals_df[(signals_df["timeframe"] == f"{interval}")]
df.sort_values(by=["symbol", 'utc_time'], inplace=True)
df.to_csv(f"signals_{interval}.csv", index=False)
df

<ipython-input-6-64dd86021997>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.sort_values(by=["symbol", 'utc_time'], inplace=True)


#     id       symbol timeframe       signal  entry_price  \
234      235    235  1000CATUSDT        1h  STRONG_SELL     0.009621   
296      297    297  1000CATUSDT        1h  STRONG_SELL     0.009602   
1490    1491   1491  1000CATUSDT        1h   STRONG_BUY     0.010320   
1638    1639   1639  1000CATUSDT        1h   STRONG_BUY     0.010530   
1767    1768   1768  1000CATUSDT        1h   STRONG_BUY     0.010600   
...      ...    ...          ...       ...          ...          ...   
27415  27416  27416      ZRXUSDT        1h  STRONG_SELL     0.253400   
28300  28301  28301      ZRXUSDT        1h  STRONG_SELL     0.247200   
29211  29212  29212      ZRXUSDT        1h  STRONG_SELL     0.244000   
30151  30152  30152      ZRXUSDT        1h  STRONG_SELL     0.241900   
30434  30435  30435      ZRXUSDT        1h  STRONG_SELL     0.240700   

       unix_timestamp                    utc_time                  local_time  
234        1740855634  2025-03-01 19:00:34.000000  2025-03-02 02:00:34.000000  
296        1740859218  2025-03-01 20:00:18.000000  2025-03-02 03:00:18.000000  
1490       1740935011  2025-03-02 17:03:31.000000  2025-03-03 00:03:31.000000  
1638       1740938482  2025-03-02 18:01:22.000000  2025-03-03 01:01:22.000000  
1767       1740942037  2025-03-02 19:00:37.000000  2025-03-03 02:00:37.000000  
...               ...                         ...                         ...  
27415      1741536006  2025-03-09 16:00:06.000000  2025-03-09 23:00:06.000000  
28300      1741539613  2025-03-09 17:00:13.000000  2025-03-10 00:00:13.000000  
29211      1741543229  2025-03-09 18:00:29.000000  2025-03-10 01:00:29.000000  
30151      1741557632  2025-03-09 22:00:32.000000  2025-03-10 05:00:32.000000  
30434      1741561207  2025-03-09 23:00:07.000000  2025-03-10 06:00:07.000000  

[12864 rows x 9 columns]